In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

import json # library to handle JSON files

!pip install geopy
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!pip install folium
import folium # map rendering library

print('Libraries imported.')

Libraries imported.


In [2]:
import urllib.request
import time
!pip install bs4
from bs4 import BeautifulSoup
from urllib.request import urlopen
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
html = urlopen(url) 
soup = BeautifulSoup(html, 'html.parser')

In [3]:
!pip install lxml
torontotable=soup.find('table',{'class':"wikitable"})
df=pd.read_html(str(torontotable))
# convert list to dataframe
df=pd.DataFrame(df[0])
print(df.head())
df.head()

  Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront


Postal Code           Borough              Neighbourhood
0         M1A      Not assigned               Not assigned
1         M2A      Not assigned               Not assigned
2         M3A        North York                  Parkwoods
3         M4A        North York           Victoria Village
4         M5A  Downtown Toronto  Regent Park, Harbourfront

In [4]:
#drop rows if Borough not assigned
df = df[df.Borough != "Not assigned"]
df.head()

Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [5]:
#group if neighborhoods have same Postal Code
df.groupby(['Postal Code','Borough'], as_index=False).agg(lambda x: ','.join(x))
df.head()

Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [6]:
# if neighborhood not assigned then rename as Borough
mask = df['Neighbourhood'] == "Not assigned"
df.loc[mask, 'Neighbourhood'] = df.loc[mask, 'Borough']
df.head()

Postal Code           Borough                                Neighbourhood
2         M3A        North York                                    Parkwoods
3         M4A        North York                             Victoria Village
4         M5A  Downtown Toronto                    Regent Park, Harbourfront
5         M6A        North York             Lawrence Manor, Lawrence Heights
6         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government

In [7]:
df_geocoor = pd.read_csv("Geospatial_Coordinates.csv")
df_geocoor.head()

Postal Code   Latitude  Longitude
0         M1B  43.806686 -79.194353
1         M1C  43.784535 -79.160497
2         M1E  43.763573 -79.188711
3         M1G  43.770992 -79.216917
4         M1H  43.773136 -79.239476

In [8]:
#merge two dataframes
df_toronto = pd.merge(df, df_geocoor, how='left', left_on = 'Postal Code', right_on = 'Postal Code')
df_toronto.head()

Postal Code           Borough                                Neighbourhood  \
0         M3A        North York                                    Parkwoods   
1         M4A        North York                             Victoria Village   
2         M5A  Downtown Toronto                    Regent Park, Harbourfront   
3         M6A        North York             Lawrence Manor, Lawrence Heights   
4         M7A  Downtown Toronto  Queen's Park, Ontario Provincial Government   

    Latitude  Longitude  
0  43.753259 -79.329656  
1  43.725882 -79.315572  
2  43.654260 -79.360636  
3  43.718518 -79.464763  
4  43.662301 -79.389494

In [9]:
#Get geographical coordinates of Toronto

address = 'Toronto, ON'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.6534817, -79.3839347.


In [10]:
# Create a map of Toronto using latitude and longitude values
map_toronto = folium.Map(location=[latitude, longitude], zoom_start=10)
map_toronto

In [11]:
# add markers to map
for lat, lng, borough, neighborhood in zip(
        df_toronto['Latitude'], 
        df_toronto['Longitude'], 
        df_toronto['Borough'], 
        df_toronto['Neighbourhood']):
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_toronto)  

map_toronto

In [18]:
#define Foursquare credentials
CLIENT_ID = 'OJSZEEBZX3AGWHEUNRUA11RBNUXPGR150OE1TUWTJHXDSTY5' # your Foursquare ID
CLIENT_SECRET = 'F3FRYPVNLSMPBHPQV1W0LMZEEPNBG5X343W2FCR24TJT0PUU' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # limit of number of venues returned by Foursquare API
radius = 500 # define radius

In [19]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
   
    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [20]:
toronto_venues = getNearbyVenues(names=df_toronto['Neighbourhood'],
                                latitudes=df_toronto['Latitude'],
                                longitudes=df_toronto['Longitude'])

Parkwoods
Victoria Village
Regent Park, Harbourfront
Lawrence Manor, Lawrence Heights
Queen's Park, Ontario Provincial Government
Islington Avenue, Humber Valley Village
Malvern, Rouge
Don Mills
Parkview Hill, Woodbine Gardens
Garden District, Ryerson
Glencairn
West Deane Park, Princess Gardens, Martin Grove, Islington, Cloverdale
Rouge Hill, Port Union, Highland Creek
Don Mills
Woodbine Heights
St. James Town
Humewood-Cedarvale
Eringate, Bloordale Gardens, Old Burnhamthorpe, Markland Wood
Guildwood, Morningside, West Hill
The Beaches
Berczy Park
Caledonia-Fairbanks
Woburn
Leaside
Central Bay Street
Christie
Cedarbrae
Hillcrest Village
Bathurst Manor, Wilson Heights, Downsview North
Thorncliffe Park
Richmond, Adelaide, King
Dufferin, Dovercourt Village
Scarborough Village
Fairview, Henry Farm, Oriole
Northwood Park, York University
East Toronto, Broadview North (Old East York)
Harbourfront East, Union Station, Toronto Islands
Little Portugal, Trinity
Kennedy Park, Ionview, East Birchmo

In [21]:
toronto_venues.shape


(2120, 7)

In [23]:
toronto_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                                
Agincourt                                                               4   
Alderwood, Long Branch                                                  8   
Bathurst Manor, Wilson Heights, Downsview North                        21   
Bayview Village                                                         4   
Bedford Park, Lawrence Manor East                                      22   
Berczy Park                                                            58   
Birch Cliff, Cliffside West                                             4   
Brockton, Parkdale Village, Exhibition Place                           22   
Business reply mail Processing Centre, South Ce...                     17   
CN Tower, King and Spadina, Railway Lands, Harb...                     17   
Caledonia-Fairbanks                                                     3   
Canada Post Gateway Processing Centre                                  14   
Cedarbrae                                                               8   
Central Bay Street                                                     61   
Christie                                                               16   
Church and Wellesley                                                   81   
Clarks Corners, Tam O'Shanter, Sullivan                                15   
Cliffside, Cliffcrest, Scarborough Village West                         2   
Commerce Court, Victoria Hotel                                        100   
Davisville                                                             35   
Davisville North                                                        7   
Del Ray, Mount Dennis, Keelsdale and Silverthorn                        4   
Don Mills                                                              25   
Dorset Park, Wexford Heights, Scarborough Town ...                      7   
Downsview                                                              13   
Dufferin, Dovercourt Village                                           16   
East Toronto, Broadview North (Old East York)                           3   
Eringate, Bloordale Gardens, Old Burnhamthorpe,...                      7   
Fairview, Henry Farm, Oriole                                           69   
First Canadian Place, Underground city                                100   
Forest Hill North & West, Forest Hill Road Park                         4   
Garden District, Ryerson                                              100   
Glencairn                                                               6   
Golden Mile, Clairlea, Oakridge                                         8   
Guildwood, Morningside, West Hill                                       8   
Harbourfront East, Union Station, Toronto Islands                     100   
High Park, The Junction South                                          25   
Hillcrest Village                                                       5   
Humber Summit                                                           3   
Humberlea, Emery                                                        3   
Humewood-Cedarvale                                                      4   
India Bazaar, The Beaches West                                         20   
Islington Avenue, Humber Valley Village                                 1   
Kennedy Park, Ionview, East Birchmount Park                             5   
Kensington Market, Chinatown, Grange Park                              63   
Kingsview Village, St. Phillips, Martin Grove G...                      3   
Lawrence Manor, Lawrence Heights                                        9   
Lawrence Park                                                           4   
Leaside                                                                31   
Little Portugal, Trinity                                               43   
Malvern, Rouge                                  

In [24]:
toronto_venues['Venue Category'].unique()[:100]

array(['Park', 'Food & Drink Shop', 'BBQ Joint', 'Hockey Arena',
       'Portuguese Restaurant', 'Coffee Shop', 'French Restaurant',
       'Bakery', 'Distribution Center', 'Breakfast Spot', 'Spa',
       'Restaurant', 'Gym / Fitness Center', 'Historic Site',
       'Chocolate Shop', 'Farmers Market', 'Dessert Shop', 'Pub',
       'Performing Arts Venue', 'Yoga Studio', 'Café', 'Theater',
       'Event Space', 'Shoe Store', 'Brewery', 'Art Gallery',
       'Cosmetics Shop', 'Asian Restaurant', 'Electronics Store',
       'Beer Store', 'Bank', 'Hotel', 'Wine Shop', 'Antique Shop',
       'Playground', 'Boutique', 'Furniture / Home Store',
       'Vietnamese Restaurant', 'Clothing Store', 'Accessories Store',
       'Athletics & Sports', 'Italian Restaurant', 'Beer Bar', 'Creperie',
       'Mexican Restaurant', 'Sushi Restaurant', 'Diner', 'Hobby Shop',
       'Burrito Place', 'Fried Chicken Joint', 'Nightclub',
       'Discount Store', 'Japanese Restaurant', 'Fast Food Restaurant',
    

In [25]:
"Gym" in toronto_venues['Venue Category'].unique()

True

In [26]:
to_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
to_onehot['Neighborhoods'] = toronto_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [to_onehot.columns[-1]] + list(to_onehot.columns[:-1])
to_onehot = to_onehot[fixed_columns]

print(to_onehot.shape)
to_onehot.head()

(2120, 273)


Neighborhoods  Accessories Store  Airport  Airport Food Court  \
0         Parkwoods                  0        0                   0   
1         Parkwoods                  0        0                   0   
2         Parkwoods                  0        0                   0   
3  Victoria Village                  0        0                   0   
4  Victoria Village                  0        0                   0   

   Airport Gate  Airport Lounge  Airport Service  Airport Terminal  \
0             0               0                0                 0   
1             0               0                0                 0   
2             0               0                0                 0   
3             0               0                0                 0   
4             0               0                0                 0   

   American Restaurant  Antique Shop  Aquarium  Art Gallery  Art Museum  \
0                    0             0         0            0           0   
1                    0             0         0            0           0   
2                    0             0         0            0           0   
3                    0             0         0            0           0   
4                    0             0         0            0           0   

   Arts & Crafts Store  Asian Restaurant  Athletics & Sports  Auto Garage  \
0                    0                 0                   0            0   
1                    0                 0                   0            0   
2                    0                 0                   0            0   
3                    0                 0                   0            0   
4                    0                 0                   0            0   

   Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  \
0              0          0           0           0       0     0    0   
1              0          0           0           0       0     0    0   
2              0          1           0           0       0     0    0   
3              0          0           0           0       0     0    0   
4              0          0           0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Stadium  Beach  \
0               0                 0                   0      0   
1               0                 0                   0      0   
2               0                 0                   0      0   
3               0                 0                   0      0   
4               0                 0                   0      0   

   Bed & Breakfast  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0                0         0           0                   0          0   
1                0         0           0                   0          0   
2                0         0           0                   0          0   
3                0         0           0                   0          0   
4                0         0           0                   0          0   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  \
0       0           0              0          0         0   
1       0           0              0          0         0   
2       0           0              0          0         0   
3       0           0              0          0         0   
4       0           0              0          0         0   

   Brazilian Restaurant  Breakfast Spot  Brewery  Bridal Shop  \
0                     0               0        0            0   
1                     0               0        0            0   
2                     0               0        0            0   
3                     0               0        0            0   
4                     0               0        0            0   

   Bubble Tea Shop  Building  Burger Joint  Burrito Place  Bus Line  \
0                0         0             0              0         0   
1                0         0             0         

In [27]:
to_grouped = to_onehot.groupby(["Neighborhoods"]).mean().reset_index()

print(to_grouped.shape)
to_grouped

(97, 273)


Neighborhoods  Accessories Store  \
0                                           Agincourt           0.000000   
1                              Alderwood, Long Branch           0.000000   
2     Bathurst Manor, Wilson Heights, Downsview North           0.000000   
3                                     Bayview Village           0.000000   
4                   Bedford Park, Lawrence Manor East           0.000000   
5                                         Berczy Park           0.000000   
6                         Birch Cliff, Cliffside West           0.000000   
7        Brockton, Parkdale Village, Exhibition Place           0.000000   
8   Business reply mail Processing Centre, South C...           0.000000   
9   CN Tower, King and Spadina, Railway Lands, Har...           0.000000   
10                                Caledonia-Fairbanks           0.000000   
11              Canada Post Gateway Processing Centre           0.000000   
12                                          Cedarbrae           0.000000   
13                                 Central Bay Street           0.000000   
14                                           Christie           0.000000   
15                               Church and Wellesley           0.000000   
16            Clarks Corners, Tam O'Shanter, Sullivan           0.000000   
17    Cliffside, Cliffcrest, Scarborough Village West           0.000000   
18                     Commerce Court, Victoria Hotel           0.000000   
19                                         Davisville           0.000000   
20                                   Davisville North           0.000000   
21   Del Ray, Mount Dennis, Keelsdale and Silverthorn           0.000000   
22                                          Don Mills           0.000000   
23  Dorset Park, Wexford Heights, Scarborough Town...           0.000000   
24                                          Downsview           0.000000   
25                       Dufferin, Dovercourt Village           0.000000   
26      East Toronto, Broadview North (Old East York)           0.000000   
27  Eringate, Bloordale Gardens, Old Burnhamthorpe...           0.000000   
28                       Fairview, Henry Farm, Oriole           0.000000   
29             First Canadian Place, Underground city           0.000000   
30    Forest Hill North & West, Forest Hill Road Park           0.000000   
31                           Garden District, Ryerson           0.000000   
32                                          Glencairn           0.000000   
33                    Golden Mile, Clairlea, Oakridge           0.000000   
34                  Guildwood, Morningside, West Hill           0.000000   
35  Harbourfront East, Union Station, Toronto Islands           0.000000   
36                      High Park, The Junction South           0.000000   
37                                  Hillcrest Village           0.000000   
38                                      Humber Summit           0.000000   
39                                   Humberlea, Emery           0.000000   
40                                 Humewood-Cedarvale           0.000000   
41                     India Bazaar, The Beaches West           0.000000   
42            Islington Avenue, Humber Valley Village           0.000000   
43        Kennedy Park, Ionview, East Birchmount Park           0.000000   
44          Kensington Market, Chinatown, Grange Park           0.000000   
45  Kingsview Village, St. Phillips, Martin Grove ...           0.000000   
46                   Lawrence Manor, Lawrence Heights           0.111111   
47                                      Lawrence Park           0.000000   
48                                            Leaside           0.000000   
49                           Little Portugal, Trinity           0.000000   
50                                     Malvern, Rouge           0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...           0.000000   
52  Mimico N

In [28]:
len(to_grouped[to_grouped["Gym"] > 0])

18

In [29]:
to_gym = to_grouped[["Neighborhoods","Gym"]]

In [30]:
to_gym.head(9)

Neighborhoods       Gym
0                                          Agincourt  0.000000
1                             Alderwood, Long Branch  0.125000
2    Bathurst Manor, Wilson Heights, Downsview North  0.000000
3                                    Bayview Village  0.000000
4                  Bedford Park, Lawrence Manor East  0.000000
5                                        Berczy Park  0.000000
6                        Birch Cliff, Cliffside West  0.000000
7       Brockton, Parkdale Village, Exhibition Place  0.045455
8  Business reply mail Processing Centre, South C...  0.000000

In [31]:
from sklearn.cluster import KMeans
toclusters = 3

to_clustering = to_gym.drop(["Neighborhoods"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=toclusters, random_state=1)
kmeans.fit_transform(to_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:20]

array([0, 2, 0, 0, 0, 0, 0, 1, 0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 1, 1],
      dtype=int32)

In [32]:
to_merged = to_gym.copy()

# add clustering labels
to_merged["Cluster Labels"] = kmeans.labels_

In [33]:
to_merged.rename(columns={"Neighborhoods": "Neighborhood"}, inplace=True)
to_merged.head(5)

Neighborhood    Gym  Cluster Labels
0                                        Agincourt  0.000               0
1                           Alderwood, Long Branch  0.125               2
2  Bathurst Manor, Wilson Heights, Downsview North  0.000               0
3                                  Bayview Village  0.000               0
4                Bedford Park, Lawrence Manor East  0.000               0

In [34]:
to_merged = to_merged.join(toronto_venues.set_index("Neighborhood"), on="Neighborhood")

print(to_merged.shape)
to_merged.head()

(2120, 9)


Neighborhood    Gym  Cluster Labels  Neighborhood Latitude  \
0               Agincourt  0.000               0              43.794200   
0               Agincourt  0.000               0              43.794200   
0               Agincourt  0.000               0              43.794200   
0               Agincourt  0.000               0              43.794200   
1  Alderwood, Long Branch  0.125               2              43.602414   

   Neighborhood Longitude                             Venue  Venue Latitude  \
0              -79.262029       Panagio's Breakfast & Lunch       43.792370   
0              -79.262029                     El Pulgarcito       43.792648   
0              -79.262029                          Twilight       43.791999   
0              -79.262029                   Commander Arena       43.794867   
1              -79.543484  Il Paesano Pizzeria & Restaurant       43.601280   

   Venue Longitude             Venue Category  
0       -79.260203             Breakfast Spot  
0       -79.259208  Latin American Restaurant  
0       -79.258584                     Lounge  
0       -79.267989               Skating Rink  
1       -79.545028                Pizza Place

In [35]:
to_merged.sort_values(["Cluster Labels"], inplace=True)
to_merged.head()

Neighborhood  Gym  Cluster Labels  \
0                           Agincourt  0.0               0   
56  North Toronto West, Lawrence Park  0.0               0   
56  North Toronto West, Lawrence Park  0.0               0   
56  North Toronto West, Lawrence Park  0.0               0   
56  North Toronto West, Lawrence Park  0.0               0   

    Neighborhood Latitude  Neighborhood Longitude  \
0               43.794200              -79.262029   
56              43.715383              -79.405678   
56              43.715383              -79.405678   
56              43.715383              -79.405678   
56              43.715383              -79.405678   

                            Venue  Venue Latitude  Venue Longitude  \
0     Panagio's Breakfast & Lunch       43.792370       -79.260203   
56  St. Clements - Yonge Parkette       43.712062       -79.404255   
56                            GAP       43.715450       -79.400089   
56                     Second Cup       43.714583       -79.400120   
56                    Tim Hortons       43.714894       -79.399776   

    Venue Category  
0   Breakfast Spot  
56            Park  
56  Clothing Store  
56            Café  
56     Coffee Shop

In [37]:
map_clusters = folium.Map(location=[lat, lng],zoom_start=14)

# set color scheme for the clusters


# add markers to the map
markers_colors={}
markers_colors[0] = 'red'
markers_colors[1] = 'blue'
markers_colors[2] = 'green'
markers_colors[3] = 'yellow'
markers_colors[4] = 'cyan'
markers_colors[5] = 'black'
for lat, lon, cluster in zip(to_merged['Neighborhood Latitude'], to_merged['Neighborhood Longitude'], to_merged['Cluster Labels']):
    
    
    folium.features.CircleMarker(
        [lat, lon],
        radius=5,
       
        color =markers_colors[cluster],
        fill_color=markers_colors[cluster],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [39]:
#Cluster 0
to_merged.loc[(to_merged['Cluster Labels'] ==0) & (to_merged['Venue Category'] == 'Gym') ]

Neighborhood       Gym  Cluster Labels  \
84  Toronto Dominion Centre, Design Exchange  0.010000               0   
76                            Stn A PO Boxes  0.020408               0   
76                            Stn A PO Boxes  0.020408               0   
31                  Garden District, Ryerson  0.010000               0   

    Neighborhood Latitude  Neighborhood Longitude  \
84              43.647177              -79.381576   
76              43.646435              -79.374846   
76              43.646435              -79.374846   
31              43.657162              -79.378937   

                                           Venue  Venue Latitude  \
84                            Equinox Bay Street       43.648100   
76                            Equinox Bay Street       43.648100   
76  GoodLife Fitness Toronto Street Women's Only       43.650400   
31  GoodLife Fitness Toronto Bell Trinity Centre       43.653436   

    Venue Longitude Venue Category  
84       -79.379989            Gym  
76       -79.379989            Gym  
76       -79.376700            Gym  
31       -79.382314            Gym

In [40]:
#Cluster 1
to_merged.loc[(to_merged['Cluster Labels'] ==1) & (to_merged['Venue Category'] == 'Gym') ]

Neighborhood       Gym  \
29             First Canadian Place, Underground city  0.040000   
52  Mimico NW, The Queensway West, South of Bloor,...  0.071429   
18                     Commerce Court, Victoria Hotel  0.040000   
29             First Canadian Place, Underground city  0.040000   
11              Canada Post Gateway Processing Centre  0.071429   
7        Brockton, Parkdale Village, Exhibition Place  0.045455   
41                     India Bazaar, The Beaches West  0.050000   
29             First Canadian Place, Underground city  0.040000   
29             First Canadian Place, Underground city  0.040000   
83                                   Thorncliffe Park  0.052632   
65                           Richmond, Adelaide, King  0.031250   
65                           Richmond, Adelaide, King  0.031250   
65                           Richmond, Adelaide, King  0.031250   
69                                 Runnymede, Swansea  0.029412   
63        Queen's Park, Ontario Provincial Government  0.027778   
19                                         Davisville  0.057143   
18                     Commerce Court, Victoria Hotel  0.040000   
19                                         Davisville  0.057143   
18                     Commerce Court, Victoria Hotel  0.040000   
18                     Commerce Court, Victoria Hotel  0.040000   
73                                     St. James Town  0.025641   
73                                     St. James Town  0.025641   

    Cluster Labels  Neighborhood Latitude  Neighborhood Longitude  \
29               1              43.648429              -79.382280   
52               1              43.628841              -79.520999   
18               1              43.648198              -79.379817   
29               1              43.648429              -79.382280   
11               1              43.636966              -79.615819   
7                1              43.636847              -79.428191   
41               1              43.668999              -79.315572   
29               1              43.648429              -79.382280   
29               1              43.648429              -79.382280   
83               1              43.705369              -79.349372   
65               1              43.650571              -79.384568   
65               1              43.650571              -79.384568   
65               1              43.650571              -79.384568   
69               1              43.651571              -79.484450   
63               1              43.662301              -79.389494   
19               1              43.704324              -79.388790   
18               1              43.648198              -79.379817   
19               1              43.704324              -79.388790   
18               1              43.648198              -79.379817   
18               1              43.648198              -79.379817   
73               1              43.651494              -79.375418   
73               1              43.651494              -79.375418   

                                                Venue  Venue Latitude  \
29                              Toronto Athletic Club       43.647360   
52                               Kingsway Boxing Club       43.627254   
18                                 Equinox Bay Street       43.648100   
29                                 Equinox Bay Street       43.648100   
11                                         LA Fitness       43.637794   
7                     Reebok Crossfit Liberty Village       43.637036   
41                                     System Fitness       43.667171   
29          GoodLife Fitness Toronto 137 Yonge Street       43.651242   
29                                 The Cambridge Club       43.651663   
83                                           Fit4Less       43.705689   
65                              Toronto Athletic Club       43.647360   
65                                 

In [41]:
#Cluster 2

to_merged.loc[(to_merged['Cluster Labels'] ==2) & (to_merged['Venue Category'] == 'Gym') ]

Neighborhood       Gym  Cluster Labels  \
1                         Alderwood, Long Branch  0.125000               2   
22                                     Don Mills  0.120000               2   
22                                     Don Mills  0.120000               2   
22                                     Don Mills  0.120000               2   
54  New Toronto, Mimico South, Humber Bay Shores  0.083333               2   

    Neighborhood Latitude  Neighborhood Longitude  \
1               43.602414              -79.543484   
22              43.745906              -79.352188   
22              43.725900              -79.340923   
22              43.725900              -79.340923   
54              43.605647              -79.501321   

                                                Venue  Venue Latitude  \
1                    Toronto Gymnastics International       43.599832   
22                                         LA Fitness       43.747665   
22                                 Fitness Connection       43.727473   
22  GoodLife Fitness North York Don Mills and Egli...       43.722704   
54                                 Crossfit Colosseum       43.604816   

    Venue Longitude Venue Category  
1        -79.542924            Gym  
22       -79.347077            Gym  
22       -79.341707            Gym  
22       -79.337508            Gym  
54       -79.507024            Gym

In [43]:
to_merged

Neighborhood       Gym  \
0                                           Agincourt  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
55           North Park, Maple Leaf Park, Upwood Park  0.000000   
55           North Park, Maple Leaf Park, Upwood Park  0.000000   
55           North Park, Maple Leaf Park, Upwood Park  0.000000   
55           North Park, Maple Leaf Park, Upwood Park  0.000000   
53                        Moore Park, Summerhill East  0.000000   
53                        Moore Park, Summerhill East  0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...  0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...  0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
51  Milliken, Agincourt North, Steeles East, L'Amo...  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
60                             Parkdale, Roncesvalles  0.000000   
56                  North Toronto West, Lawrence Park  0.000000   
59  Old Mill South, King's Mill Park, Sunnylea, Hu...  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
58                    Northwood Park, York University  0.000000   
57                Northwest, West Humber - Clairville  0.000000   
57                Northwest, West Humber - Clairville  0.000000   
57                Northwest, West Humber - Clairville  0.000000   
57                Northwest, West Humber - Clairville  0.000000   
59  Old Mill South, King's Mill Park, Sunnylea, Hu...  0.000000   
50                                     Malvern, Rouge  0.000000   
50                                     Malvern, Rouge  0.000000   
49                           Little Portugal, Trinity  0.000000   
49                           Little Portugal, Trinity  0.000000   
49                           Little Portugal, Trinity  0.000000   
49                   